In [1]:
import os
os.environ['HF_ENDPOINT'] = 'https://hf-mirror.com'
import torch
import torch.nn as nn
import timm
torch.manual_seed(3407)
torch.cuda.manual_seed(3407)
# 定义GELU_PyTorch_Tanh类
class GELU_PyTorch_Tanh(nn.Module):
    def forward(self, x):
        return 0.5 * x * (1 + torch.tanh((2 / torch.pi) ** 0.5 * (x + 0.044715 * x ** 3)))

# 定义CustomModel类
class CustomModel(nn.Module):
    def __init__(self, base_model):
        super(CustomModel, self).__init__()
        self.base_model = base_model
        
        # 定义新的分类层
        self.fc1 = nn.Linear(1536, 2048)  # EfficientNet-B1的输出维度是1536
        self.bn1 = nn.BatchNorm1d(2048)
        self.dropout1 = nn.Dropout(p=0.5)        
        self.fc2 = nn.Linear(2048, 2048)
        self.bn2 = nn.BatchNorm1d(2048)
        self.gelu = GELU_PyTorch_Tanh()
        self.dropout2 = nn.Dropout(p=0.5)
        
        self.final_fc = nn.Linear(2048, 1)  # 二分类问题，输出维度为1
        self.sigmoid = nn.Sigmoid()
        
    def forward(self, x):
        x = self.base_model(x)
        x = self.fc1(x)
        x = self.bn1(x)
        x = self.gelu(x)
        x = self.dropout1(x)
        x = self.fc2(x)
        x = self.bn2(x)
        x = self.gelu(x)
        x = self.dropout2(x)
        x = self.final_fc(x)
        x = self.sigmoid(x)
        return x

# 创建基础模型
base_model = timm.create_model('tf_efficientnet_b3.ns_jft_in1k', pretrained=True, num_classes=0)
base_model = base_model.cuda()

# 创建自定义模型
custom_model = CustomModel(base_model)
custom_model = custom_model.cuda()

# 加载保存的模型权重
checkpoint_path = "E:\\下载\\custom_model_96.64.pt"
custom_model.load_state_dict(torch.load(checkpoint_path))

<All keys matched successfully>

In [2]:
from PIL import Image
from torchvision import transforms
custom_model.eval()
transform = transforms.Compose([
    transforms.Resize((300, 300)),
    transforms.ToTensor(),
    transforms.Normalize(
        mean=[0.485, 0.456, 0.406],
        std=[0.229, 0.224, 0.225]
    )
])

In [4]:
#probabilities_list = []
image_folder = r"E:\qq文件\任务2\提取图片"
image_files = [f for f in os.listdir(image_folder) if os.path.isfile(os.path.join(image_folder, f))]

count_above_threshold = 0  # 计数大于0.5的输出数量

for image_file in image_files:
    image_path = os.path.join(image_folder, image_file)
    image = Image.open(image_path).convert('RGB')
    input_tensor = transform(image).unsqueeze(0)  # 增加batch维度
    input_tensor = input_tensor.cuda()  # 将输入张量转移到GPU

    with torch.no_grad():
        output = custom_model(input_tensor)
        
    if output.item() >= 0.07:
        count_above_threshold += 1
        print(f"Image: {image_file}, probabilities: {output}")

print(f"Number of outputs greater than 0.07: {count_above_threshold}")

Image: 0.png, probabilities: tensor([[0.9870]], device='cuda:0')
Image: 1001.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1003.png, probabilities: tensor([[0.9995]], device='cuda:0')
Image: 101.png, probabilities: tensor([[0.9978]], device='cuda:0')
Image: 1012.png, probabilities: tensor([[0.4747]], device='cuda:0')
Image: 1013.png, probabilities: tensor([[0.8764]], device='cuda:0')
Image: 1017.png, probabilities: tensor([[0.3660]], device='cuda:0')
Image: 102.png, probabilities: tensor([[0.9619]], device='cuda:0')
Image: 1021.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 1023.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 1027.png, probabilities: tensor([[0.1112]], device='cuda:0')
Image: 1029.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 1030.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1033.png, probabilities: tensor([[0.7425]], device='cuda:0')
Image: 1034.png, probabilities: tensor([[0.8482]], de

Image: 1221.png, probabilities: tensor([[0.2516]], device='cuda:0')
Image: 1223.png, probabilities: tensor([[0.9824]], device='cuda:0')
Image: 1225.png, probabilities: tensor([[0.9992]], device='cuda:0')
Image: 1226.png, probabilities: tensor([[0.1175]], device='cuda:0')
Image: 123.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 1231.png, probabilities: tensor([[0.2057]], device='cuda:0')
Image: 1237.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 124.png, probabilities: tensor([[0.1492]], device='cuda:0')
Image: 1242.png, probabilities: tensor([[0.9993]], device='cuda:0')
Image: 1243.png, probabilities: tensor([[0.1029]], device='cuda:0')
Image: 1246.png, probabilities: tensor([[0.8458]], device='cuda:0')
Image: 1248.png, probabilities: tensor([[0.9992]], device='cuda:0')
Image: 125.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1252.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1256.png, probabilities: tensor([[0.9500]], 

Image: 1511.png, probabilities: tensor([[0.9401]], device='cuda:0')
Image: 1520.png, probabilities: tensor([[0.9993]], device='cuda:0')
Image: 1523.png, probabilities: tensor([[0.7438]], device='cuda:0')
Image: 1525.png, probabilities: tensor([[0.9919]], device='cuda:0')
Image: 1528.png, probabilities: tensor([[0.9954]], device='cuda:0')
Image: 1529.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 153.png, probabilities: tensor([[0.8680]], device='cuda:0')
Image: 1535.png, probabilities: tensor([[0.9131]], device='cuda:0')
Image: 154.png, probabilities: tensor([[0.9055]], device='cuda:0')
Image: 1543.png, probabilities: tensor([[0.1096]], device='cuda:0')
Image: 155.png, probabilities: tensor([[0.7854]], device='cuda:0')
Image: 1555.png, probabilities: tensor([[0.7696]], device='cuda:0')
Image: 1565.png, probabilities: tensor([[0.8230]], device='cuda:0')
Image: 1567.png, probabilities: tensor([[0.8131]], device='cuda:0')
Image: 1570.png, probabilities: tensor([[0.9994]], 

Image: 301.png, probabilities: tensor([[0.9997]], device='cuda:0')
Image: 302.png, probabilities: tensor([[1.]], device='cuda:0')
Image: 303.png, probabilities: tensor([[0.9951]], device='cuda:0')
Image: 304.png, probabilities: tensor([[0.8944]], device='cuda:0')
Image: 308.png, probabilities: tensor([[0.2670]], device='cuda:0')
Image: 309.png, probabilities: tensor([[0.9981]], device='cuda:0')
Image: 314.png, probabilities: tensor([[0.2295]], device='cuda:0')
Image: 315.png, probabilities: tensor([[0.8504]], device='cuda:0')
Image: 317.png, probabilities: tensor([[0.3725]], device='cuda:0')
Image: 319.png, probabilities: tensor([[0.9968]], device='cuda:0')
Image: 32.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 321.png, probabilities: tensor([[0.9590]], device='cuda:0')
Image: 322.png, probabilities: tensor([[0.8992]], device='cuda:0')
Image: 326.png, probabilities: tensor([[0.2035]], device='cuda:0')
Image: 329.png, probabilities: tensor([[0.6888]], device='cuda:0')


Image: 809.png, probabilities: tensor([[0.9955]], device='cuda:0')
Image: 81.png, probabilities: tensor([[0.9188]], device='cuda:0')
Image: 810.png, probabilities: tensor([[0.3929]], device='cuda:0')
Image: 811.png, probabilities: tensor([[0.4093]], device='cuda:0')
Image: 813.png, probabilities: tensor([[0.8086]], device='cuda:0')
Image: 815.png, probabilities: tensor([[0.9792]], device='cuda:0')
Image: 817.png, probabilities: tensor([[0.1523]], device='cuda:0')
Image: 824.png, probabilities: tensor([[0.9964]], device='cuda:0')
Image: 825.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 828.png, probabilities: tensor([[0.1760]], device='cuda:0')
Image: 829.png, probabilities: tensor([[0.9984]], device='cuda:0')
Image: 833.png, probabilities: tensor([[0.3641]], device='cuda:0')
Image: 835.png, probabilities: tensor([[0.6530]], device='cuda:0')
Image: 836.png, probabilities: tensor([[0.9552]], device='cuda:0')
Image: 837.png, probabilities: tensor([[0.1598]], device='cuda:

In [3]:
image_folder = r"E:\qq文件\任务2\任务2"
image_files = [f for f in os.listdir(image_folder) if os.path.isfile(os.path.join(image_folder, f))]

count_above_threshold = 0  # 计数大于0.5的输出数量

for image_file in image_files:
    image_path = os.path.join(image_folder, image_file)
    image = Image.open(image_path).convert('RGB')
    input_tensor = transform(image).unsqueeze(0)  # 增加batch维度
    input_tensor = input_tensor.cuda()  # 将输入张量转移到GPU

    with torch.no_grad():
        output = custom_model(input_tensor)
        
    if output.item() >= 0.07:
        count_above_threshold += 1
        print(f"Image: {image_file}, probabilities: {output}")

print(f"Number of outputs greater than 0.07: {count_above_threshold}")

Image: 0.png, probabilities: tensor([[0.9870]], device='cuda:0')
Image: 1.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 100.png, probabilities: tensor([[0.7772]], device='cuda:0')
Image: 1000.png, probabilities: tensor([[0.9953]], device='cuda:0')
Image: 1001.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1002.png, probabilities: tensor([[0.9997]], device='cuda:0')
Image: 1003.png, probabilities: tensor([[0.9995]], device='cuda:0')
Image: 1004.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1005.png, probabilities: tensor([[0.9994]], device='cuda:0')
Image: 1006.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1007.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 1008.png, probabilities: tensor([[0.3588]], device='cuda:0')
Image: 101.png, probabilities: tensor([[0.9978]], device='cuda:0')
Image: 1010.png, probabilities: tensor([[0.9953]], device='cuda:0')
Image: 1012.png, probabilities: tensor([[0.4747]], devic

Image: 1133.png, probabilities: tensor([[0.9682]], device='cuda:0')
Image: 1134.png, probabilities: tensor([[0.9387]], device='cuda:0')
Image: 1135.png, probabilities: tensor([[0.9983]], device='cuda:0')
Image: 1136.png, probabilities: tensor([[0.7127]], device='cuda:0')
Image: 1137.png, probabilities: tensor([[0.9979]], device='cuda:0')
Image: 1138.png, probabilities: tensor([[0.9769]], device='cuda:0')
Image: 1139.png, probabilities: tensor([[0.9535]], device='cuda:0')
Image: 114.png, probabilities: tensor([[0.9868]], device='cuda:0')
Image: 1140.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 1141.png, probabilities: tensor([[0.9163]], device='cuda:0')
Image: 1142.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1143.png, probabilities: tensor([[0.9205]], device='cuda:0')
Image: 1145.png, probabilities: tensor([[0.9473]], device='cuda:0')
Image: 1146.png, probabilities: tensor([[0.5585]], device='cuda:0')
Image: 1148.png, probabilities: tensor([[0.7205]]

Image: 1273.png, probabilities: tensor([[0.4096]], device='cuda:0')
Image: 1274.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1275.png, probabilities: tensor([[0.9978]], device='cuda:0')
Image: 1276.png, probabilities: tensor([[0.8828]], device='cuda:0')
Image: 1277.png, probabilities: tensor([[0.8096]], device='cuda:0')
Image: 1278.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 1279.png, probabilities: tensor([[0.3595]], device='cuda:0')
Image: 128.png, probabilities: tensor([[0.8361]], device='cuda:0')
Image: 1280.png, probabilities: tensor([[0.9987]], device='cuda:0')
Image: 1281.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 1283.png, probabilities: tensor([[0.9348]], device='cuda:0')
Image: 1284.png, probabilities: tensor([[0.9871]], device='cuda:0')
Image: 1286.png, probabilities: tensor([[0.9997]], device='cuda:0')
Image: 1287.png, probabilities: tensor([[0.9835]], device='cuda:0')
Image: 1288.png, probabilities: tensor([[0.8668]]

Image: 1405.png, probabilities: tensor([[0.6104]], device='cuda:0')
Image: 1406.png, probabilities: tensor([[0.2587]], device='cuda:0')
Image: 1407.png, probabilities: tensor([[0.9122]], device='cuda:0')
Image: 1408.png, probabilities: tensor([[0.1394]], device='cuda:0')
Image: 1409.png, probabilities: tensor([[0.4847]], device='cuda:0')
Image: 141.png, probabilities: tensor([[0.9969]], device='cuda:0')
Image: 1410.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 1411.png, probabilities: tensor([[0.9092]], device='cuda:0')
Image: 1412.png, probabilities: tensor([[0.9995]], device='cuda:0')
Image: 1413.png, probabilities: tensor([[0.9852]], device='cuda:0')
Image: 1414.png, probabilities: tensor([[0.8910]], device='cuda:0')
Image: 1417.png, probabilities: tensor([[0.9390]], device='cuda:0')
Image: 1418.png, probabilities: tensor([[0.9791]], device='cuda:0')
Image: 1419.png, probabilities: tensor([[0.9737]], device='cuda:0')
Image: 142.png, probabilities: tensor([[0.9999]],

Image: 1542.png, probabilities: tensor([[0.9975]], device='cuda:0')
Image: 1543.png, probabilities: tensor([[0.1096]], device='cuda:0')
Image: 1544.png, probabilities: tensor([[0.9976]], device='cuda:0')
Image: 1545.png, probabilities: tensor([[0.8700]], device='cuda:0')
Image: 1546.png, probabilities: tensor([[0.9981]], device='cuda:0')
Image: 1547.png, probabilities: tensor([[0.1624]], device='cuda:0')
Image: 1548.png, probabilities: tensor([[0.9946]], device='cuda:0')
Image: 155.png, probabilities: tensor([[0.7854]], device='cuda:0')
Image: 1550.png, probabilities: tensor([[0.9541]], device='cuda:0')
Image: 1551.png, probabilities: tensor([[0.8675]], device='cuda:0')
Image: 1553.png, probabilities: tensor([[0.9983]], device='cuda:0')
Image: 1555.png, probabilities: tensor([[0.7696]], device='cuda:0')
Image: 1556.png, probabilities: tensor([[0.4834]], device='cuda:0')
Image: 1557.png, probabilities: tensor([[0.1552]], device='cuda:0')
Image: 1558.png, probabilities: tensor([[0.9972]]

...

Image: 433.png, probabilities: tensor([[0.0864]], device='cuda:0')
Image: 435.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 436.png, probabilities: tensor([[0.3852]], device='cuda:0')
Image: 437.png, probabilities: tensor([[0.9852]], device='cuda:0')
Image: 438.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 439.png, probabilities: tensor([[0.9996]], device='cuda:0')
Image: 44.png, probabilities: tensor([[0.5707]], device='cuda:0')
Image: 441.png, probabilities: tensor([[0.9995]], device='cuda:0')
Image: 442.png, probabilities: tensor([[0.9198]], device='cuda:0')
Image: 443.png, probabilities: tensor([[0.8540]], device='cuda:0')
Image: 445.png, probabilities: tensor([[0.7391]], device='cuda:0')
Image: 446.png, probabilities: tensor([[0.1014]], device='cuda:0')
Image: 447.png, probabilities: tensor([[0.8477]], device='cuda:0')
Image: 448.png, probabilities: tensor([[0.9466]], device='cuda:0')
Image: 449.png, probabilities: tensor([[0.9999]], device='cuda:

Image: 560.png, probabilities: tensor([[0.6037]], device='cuda:0')
Image: 561.png, probabilities: tensor([[0.2093]], device='cuda:0')
Image: 562.png, probabilities: tensor([[0.5838]], device='cuda:0')
Image: 563.png, probabilities: tensor([[0.9603]], device='cuda:0')
Image: 564.png, probabilities: tensor([[0.7786]], device='cuda:0')
Image: 565.png, probabilities: tensor([[0.9919]], device='cuda:0')
Image: 566.png, probabilities: tensor([[0.9863]], device='cuda:0')
Image: 568.png, probabilities: tensor([[0.9985]], device='cuda:0')
Image: 569.png, probabilities: tensor([[0.9424]], device='cuda:0')
Image: 571.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 572.png, probabilities: tensor([[0.4745]], device='cuda:0')
Image: 574.png, probabilities: tensor([[0.9997]], device='cuda:0')
Image: 575.png, probabilities: tensor([[0.9999]], device='cuda:0')
Image: 576.png, probabilities: tensor([[0.6552]], device='cuda:0')
Image: 579.png, probabilities: tensor([[0.0927]], device='cuda

Image: 702.png, probabilities: tensor([[0.9996]], device='cuda:0')
Image: 703.png, probabilities: tensor([[0.9979]], device='cuda:0')
Image: 704.png, probabilities: tensor([[0.3500]], device='cuda:0')
Image: 705.png, probabilities: tensor([[0.8909]], device='cuda:0')
Image: 706.png, probabilities: tensor([[0.9782]], device='cuda:0')
Image: 707.png, probabilities: tensor([[0.9987]], device='cuda:0')
Image: 708.png, probabilities: tensor([[0.1519]], device='cuda:0')
Image: 709.png, probabilities: tensor([[0.9775]], device='cuda:0')
Image: 71.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 713.png, probabilities: tensor([[0.9862]], device='cuda:0')
Image: 718.png, probabilities: tensor([[0.9453]], device='cuda:0')
Image: 719.png, probabilities: tensor([[0.1558]], device='cuda:0')
Image: 72.png, probabilities: tensor([[0.9986]], device='cuda:0')
Image: 720.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 721.png, probabilities: tensor([[0.9641]], device='cuda:0

Image: 832.png, probabilities: tensor([[0.7373]], device='cuda:0')
Image: 833.png, probabilities: tensor([[0.3641]], device='cuda:0')
Image: 834.png, probabilities: tensor([[0.8001]], device='cuda:0')
Image: 835.png, probabilities: tensor([[0.6530]], device='cuda:0')
Image: 836.png, probabilities: tensor([[0.9552]], device='cuda:0')
Image: 837.png, probabilities: tensor([[0.1598]], device='cuda:0')
Image: 838.png, probabilities: tensor([[0.9871]], device='cuda:0')
Image: 839.png, probabilities: tensor([[0.9956]], device='cuda:0')
Image: 84.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 840.png, probabilities: tensor([[0.7139]], device='cuda:0')
Image: 841.png, probabilities: tensor([[0.4956]], device='cuda:0')
Image: 842.png, probabilities: tensor([[0.9958]], device='cuda:0')
Image: 843.png, probabilities: tensor([[0.1795]], device='cuda:0')
Image: 845.png, probabilities: tensor([[0.9994]], device='cuda:0')
Image: 846.png, probabilities: tensor([[0.9997]], device='cuda:

Image: 970.png, probabilities: tensor([[0.9907]], device='cuda:0')
Image: 971.png, probabilities: tensor([[0.9974]], device='cuda:0')
Image: 972.png, probabilities: tensor([[0.9998]], device='cuda:0')
Image: 973.png, probabilities: tensor([[0.9747]], device='cuda:0')
Image: 974.png, probabilities: tensor([[0.8266]], device='cuda:0')
Image: 975.png, probabilities: tensor([[0.9842]], device='cuda:0')
Image: 976.png, probabilities: tensor([[0.9994]], device='cuda:0')
Image: 977.png, probabilities: tensor([[0.9891]], device='cuda:0')
Image: 978.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 979.png, probabilities: tensor([[0.8647]], device='cuda:0')
Image: 98.png, probabilities: tensor([[0.9980]], device='cuda:0')
Image: 981.png, probabilities: tensor([[1.0000]], device='cuda:0')
Image: 982.png, probabilities: tensor([[0.9880]], device='cuda:0')
Image: 983.png, probabilities: tensor([[0.9217]], device='cuda:0')
Image: 984.png, probabilities: tensor([[0.5426]], device='cuda:

In [5]:
import pandas as pd
image_folder = r"E:\qq文件\任务2\任务2"
image_files = [f for f in os.listdir(image_folder) if os.path.isfile(os.path.join(image_folder, f))]

results = []  # 用于存储结果的列表

for image_file in image_files:
    image_path = os.path.join(image_folder, image_file)
    image = Image.open(image_path).convert('RGB')
    input_tensor = transform(image).unsqueeze(0)  # 增加batch维度
    input_tensor = input_tensor.cuda()  # 将输入张量转移到GPU

    with torch.no_grad():
        output = custom_model(input_tensor)

    classification = 1 if output.item() >= 0.07 else 0  # 根据阈值进行分类
    results.append([image_file, classification])

# 将结果保存到CSV文件
df = pd.DataFrame(results, columns=['Image Name', 'Classification'])
df.to_csv('classification_results_0.07.csv', index=False) 

print("Classification results saved to classification_results.csv")

Classification results saved to classification_results.csv


In [6]:
import pandas as pd

def sort_by_number(filename):
  """提取文件名中的数字部分。"""
  return int(filename.split('.')[0])

def remove_png(filename):
  """移除 .png 后缀"""
  return filename[:-4]

# 读取 CSV 文件, 指定列名和标题行
df = pd.read_csv('classification_results_0.07.csv', names=['Image Name', 'Classification'], header=0) 

# 移除 .png 后缀
df['Image Name'] = df['Image Name'].apply(remove_png) 

# 按照数字大小排序
df['number'] = df['Image Name'].apply(sort_by_number)
df.sort_values(by='number', inplace=True)

# 删除辅助列
df.drop('number', axis=1, inplace=True)  

# 修改标题
df.columns = ['id', 'label'] 

# 保存排序后的文件列表
df.to_csv('sorted_file_list.csv', header=True, index=False)  # 保存时保留标题行